In [1]:
from langchain.agents import Tool, AgentExecutor, BaseMultiActionAgent
from langchain import OpenAI, SerpAPIWrapper

In [2]:
def random_word(query: str) -> str:
    print("\nNow I'm doing this!")
    return f"{query}, foo"

In [3]:
search = SerpAPIWrapper()
tools = [
    Tool(
        name = "Search",
        func=search.run,
        description="useful for when you need to answer questions about current events"
    ),
    Tool(
        name = "RandomWord",
        func=random_word,
        description="call this to get a random word.",
    )
]

In [4]:
from langchain.tools import tool

@tool
def tool1(event) -> str:
    """这里必须添加描述，不然AssertionError: Function must have a docstring if description not provided."""
    return "111"

from langchain.tools import tool

@tool
def tool2(event) -> str:
    """这里必须添加描述，不然AssertionError: Function must have a docstring if description not provided."""
    return "222"

tools = [tool1, tool2]

In [5]:
from typing import List, Tuple, Any, Union
from langchain.schema import AgentAction, AgentFinish

class FakeAgent(BaseMultiActionAgent):
    """Fake Custom Agent."""
    
    @property
    def input_keys(self):
        return ["input"]
    
    def plan(
        self, intermediate_steps: List[Tuple[AgentAction, str]], **kwargs: Any
    ) -> Union[List[AgentAction], AgentFinish]:
        """Given input, decided what to do.

        Args:
            intermediate_steps: Steps the LLM has taken to date,
                along with observations
            **kwargs: User inputs.

        Returns:
            Action specifying what tool to use.
        """
        print("lizhen0",intermediate_steps)
        if len(intermediate_steps) == 0:
            print("lizhen1",intermediate_steps)
            return [
                AgentAction(tool="tool1", tool_input=kwargs["input"], log=""),
                AgentAction(tool="tool2", tool_input=kwargs["input"], log=""),
            ]
        else:
            for tuple in intermediate_steps:
                print(tuple[0].tool, tuple[1])
            return AgentFinish(return_values={"output": "bar"}, log="")

    async def aplan(
        self, intermediate_steps: List[Tuple[AgentAction, str]], **kwargs: Any
    ) -> Union[List[AgentAction], AgentFinish]:
        """Given input, decided what to do.

        Args:
            intermediate_steps: Steps the LLM has taken to date,
                along with observations
            **kwargs: User inputs.

        Returns:
            Action specifying what tool to use.
        """
        if len(intermediate_steps) == 0:
            return [
                AgentAction(tool="tool1", tool_input=kwargs["input"], log=""),
                AgentAction(tool="tool2", tool_input=kwargs["input"], log=""),
            ]
        else:
            return AgentFinish(return_values={"output": "bar"}, log="")

In [6]:
agent = FakeAgent()

In [7]:
agent_executor = AgentExecutor.from_agent_and_tools(agent=agent, tools=tools, verbose=True)

In [8]:
agent_executor.run("How many people live in canada as of 2023?")



> Entering new AgentExecutor chain...
lizhen0 []
lizhen1 []
111222lizhen0 [(AgentAction(tool='tool1', tool_input='How many people live in canada as of 2023?', log=''), '111'), (AgentAction(tool='tool2', tool_input='How many people live in canada as of 2023?', log=''), '222')]
tool1 111
tool2 222


> Finished chain.


'bar'